In [1]:
import json, os

from llama_index.core import SimpleDirectoryReader
from llama_index.core.node_parser import SentenceSplitter
from llama_index.core.schema import MetadataMode

In [2]:
from llama_index.finetuning.embeddings.common import (
    EmbeddingQAFinetuneDataset,
    generate_qa_embedding_pairs,
)
from llama_index.finetuning import SentenceTransformersFinetuneEngine

In [3]:
from llama_index.embeddings.openai.base import OpenAIEmbedding

In [4]:
from llama_index.core import ServiceContext, VectorStoreIndex

In [5]:
from llama_index.core.schema import TextNode

In [6]:
from tqdm.notebook import tqdm
import pandas as pd

In [7]:
from sentence_transformers.evaluation import InformationRetrievalEvaluator
from sentence_transformers import SentenceTransformer
from pathlib import Path

In [8]:
from llama_index.llms.openai import OpenAI

In [9]:
TRAIN_FILES = ["../raw_documents/HI_Knowledge_Base.pdf",
               "../raw_documents/HI Chapter Summary Version 1.3.pdf"]
VAL_FILES = ["../raw_documents/qna.txt",
             "../raw_documents/conversation_examples.txt",
             "../raw_documents/answers.txt"]

### based on all docs
TRAIN_CORPUS_FPATH = "../data/train_corpus_advanced.json"

### based on ../raw_documents/HI Chapter Summary Version 1.3.pdf
VAL_CORPUS_FPATH = "../data/val_corpus.json"

In [10]:
def load_corpus(files, verbose=False):
    if verbose:
        print(f"Loading files {files}")

    reader = SimpleDirectoryReader(input_files=files)
    docs = reader.load_data()
    if verbose:
        print(f"Loaded {len(docs)} docs")

    parser = SentenceSplitter()
    nodes = parser.get_nodes_from_documents(docs, show_progress=verbose)

    if verbose:
        print(f"Parsed {len(nodes)} nodes")

    return nodes

In [11]:
if not os.path.exists(TRAIN_CORPUS_FPATH):
    train_nodes = load_corpus(TRAIN_FILES, verbose=True)
    print("generating qa embedding pairs for training data..")
    train_dataset = generate_qa_embedding_pairs(
        llm=OpenAI(model="gpt-3.5-turbo-1106"), nodes=train_nodes
    )
    train_dataset.save_json(TRAIN_CORPUS_FPATH)
else:
    print("load qa embedding training pairs from saved corpus file..")
    train_dataset = EmbeddingQAFinetuneDataset.from_json(TRAIN_CORPUS_FPATH)

if not os.path.exists(VAL_CORPUS_FPATH):
    val_nodes = load_corpus(VAL_FILES, verbose=True)
    print("generating qa embedding pairs for validation data..")
    val_dataset = generate_qa_embedding_pairs(
        llm=OpenAI(model="gpt-3.5-turbo-1106"), nodes=val_nodes
    )
    val_dataset.save_json(VAL_CORPUS_FPATH)
else:
    print("load qa embedding validation pairs from saved corpus file..")
    val_dataset = EmbeddingQAFinetuneDataset.from_json(VAL_CORPUS_FPATH)

load qa embedding training pairs from saved corpus file..
load qa embedding validation pairs from saved corpus file..


In [12]:
finetune_engine = SentenceTransformersFinetuneEngine(
    train_dataset,
    model_id="BAAI/bge-small-en-v1.5",
    model_output_path="../models/fine-tuned-embeddings-advanced",
    batch_size=5,
    val_dataset=val_dataset
)

README.md:   0%|          | 0.00/94.8k [00:00<?, ?B/s]

In [13]:
finetune_engine.finetune()

Epoch:   0%|          | 0/2 [00:00<?, ?it/s]

Iteration:   0%|          | 0/268 [00:00<?, ?it/s]

Iteration:   0%|          | 0/268 [00:00<?, ?it/s]

In [14]:
embed_model = finetune_engine.get_finetuned_model()

In [15]:
embed_model

HuggingFaceEmbedding(model_name='../models/fine-tuned-embeddings-advanced', embed_batch_size=10, callback_manager=<llama_index.core.callbacks.base.CallbackManager object at 0x29f61adf0>, tokenizer_name='../models/fine-tuned-embeddings-advanced', max_length=512, pooling=<Pooling.CLS: 'cls'>, normalize=True, query_instruction=None, text_instruction=None, cache_folder=None)

In [16]:
fine_tuned_embed_model = SentenceTransformer("../models/fine-tuned-embeddings-advanced")

In [17]:
def evaluate(
    dataset,
    embed_model,
    top_k=5,
    verbose=False,
):
    corpus = dataset.corpus
    queries = dataset.queries
    relevant_docs = dataset.relevant_docs

    service_context = ServiceContext.from_defaults(embed_model=embed_model)
    nodes = [TextNode(id_=id_, text=text) for id_, text in corpus.items()]
    index = VectorStoreIndex(
        nodes, service_context=service_context, show_progress=True
    )
    retriever = index.as_retriever(similarity_top_k=top_k)

    eval_results = []
    for query_id, query in tqdm(queries.items()):
        retrieved_nodes = retriever.retrieve(query)
        retrieved_ids = [node.node.node_id for node in retrieved_nodes]
        expected_id = relevant_docs[query_id][0]
        is_hit = expected_id in retrieved_ids  # assume 1 relevant doc

        eval_result = {
            "is_hit": is_hit,
            "retrieved": retrieved_ids,
            "expected": expected_id,
            "query": query_id,
        }
        eval_results.append(eval_result)
    return eval_results

In [18]:
def evaluate_st(
    dataset,
    model_id,
    name,
):
    corpus = dataset.corpus
    queries = dataset.queries
    relevant_docs = dataset.relevant_docs

    evaluator = InformationRetrievalEvaluator(
        queries, corpus, relevant_docs, name=name
    )
    model = SentenceTransformer(model_id)
    output_path = "../results/"
    Path(output_path).mkdir(exist_ok=True, parents=True)
    return evaluator(model, output_path=output_path)

### Using OpenAI Ada embedding

In [19]:
ada = OpenAIEmbedding()
ada_val_results = evaluate(val_dataset, ada)

/var/folders/9p/zqv8rk793ts9cxxfr66p40sh0000gn/T/ipykernel_34681/2760886022.py:11: DeprecationWarning: Call to deprecated class method from_defaults. (ServiceContext is deprecated, please use `llama_index.settings.Settings` instead.) -- Deprecated since version 0.10.0.
  service_context = ServiceContext.from_defaults(embed_model=embed_model)


Generating embeddings:   0%|          | 0/100 [00:00<?, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


  0%|          | 0/200 [00:00<?, ?it/s]

In [20]:
df_ada = pd.DataFrame(ada_val_results)

In [21]:
df_ada[:5]

is_hit                                          retrieved  \
0   False  [5b9cd986-33dc-46f1-abae-e4e1dc9e3629, c3c1804...   
1    True  [6a756f03-638d-480d-8222-1a6bf3790e3c, c3c1804...   
2    True  [c83dbd8a-7e62-445e-8c12-a8ad604ff65e, 2177824...   
3    True  [c83dbd8a-7e62-445e-8c12-a8ad604ff65e, 2177824...   
4    True  [21778248-2ed9-4147-bdb0-a60337a1a599, c83dbd8...   

                               expected                                 query  
0  6a756f03-638d-480d-8222-1a6bf3790e3c  011d84b2-0c26-4c5c-89d1-2a85498f30e0  
1  6a756f03-638d-480d-8222-1a6bf3790e3c  70c5ddd7-eb86-4a41-af70-a23d2392f48d  
2  c83dbd8a-7e62-445e-8c12-a8ad604ff65e  a8f4290a-1281-4272-aab9-bf089954a45e  
3  c83dbd8a-7e62-445e-8c12-a8ad604ff65e  c1ef991a-1cc6-4dbf-b179-2df688c84301  
4  21778248-2ed9-4147-bdb0-a60337a1a599  1ce25e78-c1e1-487e-9455-9418baa0b60c

In [22]:
hit_rate_ada = df_ada["is_hit"].mean()
hit_rate_ada, len(df_ada)

(0.95, 200)

### Using BAAI bge-small model without fine-tuning

In [23]:
bge = "local:BAAI/bge-small-en-v1.5"
bge_val_results = evaluate(val_dataset, bge)

/var/folders/9p/zqv8rk793ts9cxxfr66p40sh0000gn/T/ipykernel_34681/2760886022.py:11: DeprecationWarning: Call to deprecated class method from_defaults. (ServiceContext is deprecated, please use `llama_index.settings.Settings` instead.) -- Deprecated since version 0.10.0.
  service_context = ServiceContext.from_defaults(embed_model=embed_model)


Generating embeddings:   0%|          | 0/100 [00:00<?, ?it/s]

  0%|          | 0/200 [00:00<?, ?it/s]

In [24]:
df_bge = pd.DataFrame(bge_val_results)

In [25]:
df_bge[:5]

is_hit                                          retrieved  \
0   False  [69a5696d-0c0e-482a-b6a9-f7b87f19945f, fa650c7...   
1    True  [6a756f03-638d-480d-8222-1a6bf3790e3c, d89a649...   
2    True  [c83dbd8a-7e62-445e-8c12-a8ad604ff65e, 2177824...   
3    True  [c83dbd8a-7e62-445e-8c12-a8ad604ff65e, ad2e3eb...   
4    True  [21778248-2ed9-4147-bdb0-a60337a1a599, c83dbd8...   

                               expected                                 query  
0  6a756f03-638d-480d-8222-1a6bf3790e3c  011d84b2-0c26-4c5c-89d1-2a85498f30e0  
1  6a756f03-638d-480d-8222-1a6bf3790e3c  70c5ddd7-eb86-4a41-af70-a23d2392f48d  
2  c83dbd8a-7e62-445e-8c12-a8ad604ff65e  a8f4290a-1281-4272-aab9-bf089954a45e  
3  c83dbd8a-7e62-445e-8c12-a8ad604ff65e  c1ef991a-1cc6-4dbf-b179-2df688c84301  
4  21778248-2ed9-4147-bdb0-a60337a1a599  1ce25e78-c1e1-487e-9455-9418baa0b60c

In [26]:
hit_rate_bge = df_bge["is_hit"].mean()
hit_rate_bge, len(df_bge)

(0.915, 200)

In [27]:
evaluate_st(val_dataset, "BAAI/bge-small-en-v1.5", name="bge")

0.7955697668171072

### Using BAAI bge-small model with `fine-tuning`

In [28]:
finetuned = "local:../models/fine-tuned-embeddings-advanced"
val_results_finetuned = evaluate(val_dataset, finetuned)

/var/folders/9p/zqv8rk793ts9cxxfr66p40sh0000gn/T/ipykernel_34681/2760886022.py:11: DeprecationWarning: Call to deprecated class method from_defaults. (ServiceContext is deprecated, please use `llama_index.settings.Settings` instead.) -- Deprecated since version 0.10.0.
  service_context = ServiceContext.from_defaults(embed_model=embed_model)


Generating embeddings:   0%|          | 0/100 [00:00<?, ?it/s]

  0%|          | 0/200 [00:00<?, ?it/s]

In [29]:
df_finetuned = pd.DataFrame(val_results_finetuned)

In [30]:
hit_rate_finetuned = df_finetuned["is_hit"].mean()
hit_rate_finetuned

0.97

In [31]:
evaluate_st(val_dataset, "../models/fine-tuned-embeddings-advanced", name="finetuned")

0.8835191391941393

### Summary

In [32]:
df_ada["model"] = "ada"
df_bge["model"] = "bge"
df_finetuned["model"] = "fine_tuned"

In [33]:
df_all = pd.concat([df_ada, df_bge, df_finetuned])
df_all.groupby("model").mean("is_hit")

is_hit
model             
ada          0.950
bge          0.915
fine_tuned   0.970

In [35]:
df_st_bge = pd.read_csv(
    "../results/Information-Retrieval_evaluation_bge_results.csv"
)
df_st_finetuned = pd.read_csv(
    "../results/Information-Retrieval_evaluation_finetuned_results.csv"
)

In [36]:
df_st_bge["model"] = "bge"
df_st_finetuned["model"] = "fine_tuned"
df_st_all = pd.concat([df_st_bge, df_st_finetuned])
df_st_all = df_st_all.set_index("model")
df_st_all

epoch  steps  cos_sim-Accuracy@1  cos_sim-Accuracy@3  \
model                                                              
bge            -1     -1               0.705               0.865   
bge            -1     -1               0.705               0.865   
bge            -1     -1               0.705               0.865   
fine_tuned     -1     -1               0.790               0.900   
fine_tuned     -1     -1               0.790               0.900   
fine_tuned     -1     -1               0.770               0.910   
fine_tuned     -1     -1               0.815               0.945   

            cos_sim-Accuracy@5  cos_sim-Accuracy@10  cos_sim-Precision@1  \
model                                                                      
bge                      0.920                 0.96                0.705   
bge                      0.920                 0.96                0.705   
bge                      0.920                 0.96                0.705   
fine_tuned               0.970                 0.98                0.790   
fine_tuned               0.970                 0.98                0.790   
fine_tuned               0.965                 0.98                0.770   
fine_tuned               0.970                 0.99                0.815   

            cos_sim-Recall@1  cos_sim-Precision@3  cos_sim-Recall@3  ...  \
model                                                                ...   
bge                    0.705             0.288333             0.865  ...   
bge                    0.705             0.288333             0.865  ...   
bge                    0.705             0.288333             0.865  ...   
fine_tuned             0.790             0.300000             0.900  ...   
fine_tuned             0.790             0.300000             0.900  ...   
fine_tuned             0.770             0.303333             0.910  ...   
fine_tuned             0.815             0.315000             0.945  ...   

            dot_score-Recall@1  dot_score-Precision@3  dot_score-Recall@3  \
model                                                                       
bge                      0.705               0.288333               0.865   
bge                      0.705               0.288333               0.865   
bge                      0.705               0.288333               0.865   
fine_tuned               0.790               0.300000               0.900   
fine_tuned               0.790               0.300000               0.900   
fine_tuned               0.770               0.303333               0.910   
fine_tuned               0.815               0.315000               0.945   

            dot_score-Precision@5  dot_score-Recall@5  dot_score-Precision@10  \
model                                                                           
bge                         0.184               0.920                   0.096   
bge                         0.184               0.920                   0.096   
bge                         0.184               0.920                   0.096   
fine_tuned                  0.194               0.970                   0.098   
fine_tuned                  0.194               0.970                   0.098   
fine_tuned                  0.193               0.965                   0.098   
fine_tuned                  0.194               0.970                   0.099   

            dot_score-Recall@10  dot_score-MRR@10  dot_score-NDCG@10  \
model                                                                  
bge                        0.96          0.792935           0.833595   
bge                        0.96          0.792935           0.833595   
bge                        0.96          0.792935           0.833595   
fine_tuned                 0.98          0.856264           0.886738   
fine_tuned                 0.98          0.856264           0.886738   
fine_tuned                 0.98          0.847542           0.880388   
fine_tuned                 0.